In [1]:

## Libraries Prequisities
!pip install scikit-learn
!pip install numpy==1.16.1

     |████████████████████████████████| 17.3MB 194kB/s 
ERROR: tensorflow-model-optimization 0.2.1 requires enum34~=1.1, which is not installed.
ERROR: tensorflow-federated 0.12.0 has requirement tensorflow~=2.1.0, but you'll have tensorflow 1.15.0 which is incompatible.
ERROR: tensorflow-federated 0.12.0 has requirement tensorflow-addons~=0.7.0, but you'll have tensorflow-addons 0.8.3 which is incompatible.
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.8.3 which is incompatible.
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
  Found existing installation: numpy 1.18.2
    Uninstalling numpy-1.18.2:
      Successfully uninstalled numpy-1.18.2


In [1]:
!pip install hpelm

     |████████████████████████████████| 51kB 3.1MB/s 
     |████████████████████████████████| 163kB 12.7MB/s 


In [0]:
import hpelm

In [3]:
import numpy as np
import random
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.metrics.classification import accuracy_score, recall_score, f1_score
import scipy.stats as st

/usr/local/lib/python3.6/dist-packages/sklearn/utils/deprecation.py:144: FutureWarning: The sklearn.metrics.classification module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.metrics. Anything that cannot be imported from sklearn.metrics is now part of the private API.
  warnings.warn(message, FutureWarning)


In [4]:
%tensorflow_version 2.x
import tensorflow as tf
print(tf.__version__)
print(tf.test.gpu_device_name())
print("Num GPUs Available: ", len(tf.config.experimental.list_physical_devices('GPU')))

TensorFlow 2.x selected.
2.1.0
/device:GPU:0
Num GPUs Available:  1


In [0]:
from tensorflow.keras.callbacks import Callback

In [6]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
np.random.seed(12227)

In [0]:
def DataPreparation(data_input_file):
  print('Jian Sun et al. 2018 {}'.format(data_input_file))
  data = np.load(data_input_file)
  X = data['X']
  # X = X[:, 0, :, :]
  Y = data['y']
  folds = data['folds']
  # classes_number = Y.shape[1]
  # Y = np.argmax(Y, axis=1)
  return X,Y,folds

In [0]:
x,y,f=DataPreparation('/content/drive/My Drive/Computer_vision_project/data/LOSO/WHARF.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/LOSO/WHARF.npz


In [0]:
x=x[0,0,:,:]

In [0]:
y.shape

(3871, 12)

In [0]:
x.shape

(160, 3)

In [0]:
x

array([[30., 40., 51.],
       [30., 41., 51.],
       [31., 41., 51.],
       [29., 42., 51.],
       [30., 43., 52.],
       [30., 40., 52.],
       [31., 41., 52.],
       [32., 39., 52.],
       [29., 38., 52.],
       [29., 38., 50.],
       [28., 40., 50.],
       [31., 38., 51.],
       [30., 39., 51.],
       [30., 39., 50.],
       [31., 39., 51.],
       [30., 38., 52.],
       [29., 39., 53.],
       [31., 38., 52.],
       [29., 39., 53.],
       [31., 37., 53.],
       [29., 38., 53.],
       [29., 42., 51.],
       [31., 38., 53.],
       [30., 37., 53.],
       [31., 42., 52.],
       [30., 39., 51.],
       [29., 38., 53.],
       [29., 41., 51.],
       [27., 40., 50.],
       [27., 41., 49.],
       [26., 42., 48.],
       [25., 46., 49.],
       [25., 42., 49.],
       [24., 42., 49.],
       [25., 41., 48.],
       [24., 42., 49.],
       [24., 42., 50.],
       [23., 43., 50.],
       [22., 40., 48.],
       [22., 43., 48.],
       [22., 42., 48.],
       [17., 42.

In [0]:
def ReportAccuracies(avg_acc, avg_recall,avg_f1):
  ic_acc = st.t.interval(0.9, len(avg_acc) - 1, loc=np.mean(avg_acc), scale=st.sem(avg_acc))
  ic_recall = st.t.interval(0.9, len(avg_recall) - 1, loc=np.mean(avg_recall), scale=st.sem(avg_recall))
  ic_f1 = st.t.interval(0.9, len(avg_f1) - 1, loc=np.mean(avg_f1), scale=st.sem(avg_f1))
  print('Mean Accuracy[{:.4f}] IC [{:.4f}, {:.4f}]'.format(np.mean(avg_acc), ic_acc[0], ic_acc[1]))
  print('Mean Recall[{:.4f}] IC [{:.4f}, {:.4f}]'.format(np.mean(avg_recall), ic_recall[0], ic_recall[1]))
  print('Mean F1[{:.4f}] IC [{:.4f}, {:.4f}]'.format(np.mean(avg_f1), ic_f1[0], ic_f1[1]))

In [0]:
def RunJian_Sun(data_input_file):
  X,Y,folds,= DataPreparation(data_input_file)
  # idx = [3, 5, 8, 11, 14, 17, 20] #For MHEALTH
  # idx = [1, 4, 7, 10, 13, 14, 17, 20, 23, 26, 27, 30, 33, 36]#For PAMAP2P
  # idx = [val for val in idx for _ in (0, 1)] #Vertical Kernel-1
  # X = zero_padding_MHEALTH(X)
  avg_acc, avg_recall,avg_f1= Train(X,Y,folds)
  ReportAccuracies(avg_acc, avg_recall,avg_f1 )

In [0]:
def RunJian_Sun_ELM(data_input_file):
  X,Y,folds,= DataPreparation(data_input_file)
  # idx = [3, 5, 8, 11, 14, 17, 20] #For MHEALTH
  # idx = [1, 4, 7, 10, 13, 14, 17, 20, 23, 26, 27, 30, 33, 36]#For PAMAP2P
  # idx = [val for val in idx for _ in (0, 1)] #Vertical Kernel-1
  # X = zero_padding_MHEALTH(X)
  avg_acc, avg_recall,avg_f1= Train_ELM(X,Y,folds)
  ReportAccuracies(avg_acc, avg_recall,avg_f1 )

In [0]:
# def build_model_1(row,col,num_classes):

  
 
#   layers = [
#         tf.keras.layers.TimeDistributed(tf.keras.layers.Conv2D(filters=1,kernel_size=(5,1),strides=1), input_shape=(None,row,col,1)),
#         tf.keras.layers.TimeDistributed(tf.keras.layers.Conv2D(filters=1,kernel_size=(5,1), strides=1)),
#         tf.keras.layers.TimeDistributed(tf.keras.layers.Conv2D(filters=1,kernel_size=(5,1), strides=1)),
#         tf.keras.layers.TimeDistributed(tf.keras.layers.Conv2D(filters=1,kernel_size=(5,1), strides=1)),
#         tf.keras.layers.TimeDistributed(tf.keras.layers.Flatten()),
        
#         tf.keras.layers.LSTM(128,return_sequences=True),
#         tf.keras.layers.LSTM(128),      
                  

       

       
        
       
#         tf.keras.layers.Dense(num_classes, activation = 'softmax')
#     ]
    
#   model = tf.keras.Sequential(layers)
#   return model

In [0]:
def build_model_1(row,col,num_classes):

  
 
  layers = [
       tf.keras.layers.Conv2D(filters=1,kernel_size=(5, 1),strides=1, input_shape=(1,row,col)),
       tf.keras.layers.Conv2D(filters=1,kernel_size=(5, 1), strides=1),
        tf.keras.layers.Conv2D(filters=1,kernel_size=(5, 1), strides=1),
       tf.keras.layers.Conv2D(filters=1,kernel_size=(5, 1), strides=1),
       tf.keras.layers.TimeDistributed(tf.keras.layers.Flatten()),
      #  tf.keras.layers.Reshape((col,row)),
     
        
        tf.keras.layers.LSTM(128,return_sequences=True),
        tf.keras.layers.LSTM(128),      
                  

       

       
        
       
        tf.keras.layers.Dense(num_classes, activation = 'softmax')
    ]
    
  model = tf.keras.Sequential(layers)
  return model

In [0]:
# ELM from https://github.com/sasayabaku/cnn-elm/blob/master/elm_cnn_mnist.py
def hidden_layer_generate(cnn_model,X):

    """
    CNNの中間層の出力を取得するモデルの構築
    :param cnn_model: CNNモデル
    :return:
    """

    layer_name = 'flatten_1'
    hidden_layer_model = tf.keras.models.Model(inputs=cnn_model.input, outputs=cnn_model.layers[6].output)

    cnn_train_result = hidden_layer_model.predict(X)

    return hidden_layer_model, cnn_train_result
def elm_model_generate(hidden_layer_cnn_lstm, y,x,num_classes):

    """
    ELMモデルの構築
    """

    target_train_oh = tf.keras.utils.to_categorical(y, num_classes)
    print(target_train_oh.shape)

    elm_model = hpelm.elm.ELM(hidden_layer_cnn_lstm.shape[1], num_classes)
    print(hidden_layer_cnn_lstm.shape)
    elm_model.add_neurons(128, func='sigm')

    elm_model.train(hidden_layer_cnn_lstm, y, 'c')

    return elm_model

In [0]:
def predict_ELM(cnn_part, elm_part, X):

  

  cnn_result = cnn_part.predict(X)
  elm_result = elm_part.predict(cnn_result)
  return elm_result

  

In [0]:
def Train_ELM(X,y,folds):
  avg_acc = []
  avg_recall = []
  avg_f1 = []
  n_class = y.shape[1]
  _,_, img_rows, img_cols = X.shape
  print(X.shape)
  for i in range(0, len(folds)):
    train_idx = folds[i][0]
    test_idx = folds[i][1]
    X_train = X[train_idx]
    X_test = X[test_idx]
    model=build_model_1(img_rows,img_cols,n_class)
    # print(model.summary)
    model.compile(loss='categorical_crossentropy', metrics=['accuracy'], optimizer='SGD')
    model.fit(X_train, y[train_idx], batch_size=64, epochs=300)
    hidden_layer_model, cnn_train_result=hidden_layer_generate(model,X_train)
    elm_model=elm_model_generate(cnn_train_result,y[train_idx],X_train,n_class)
    
    
    y_pred = predict_ELM(hidden_layer_model,elm_model,X_test)
    y_pred = np.argmax(y_pred, axis=1)
    y_true = np.argmax(y[test_idx], axis=1)
    acc_fold = accuracy_score(y_true, y_pred)
    avg_acc.append(acc_fold)
    recall_fold = recall_score(y_true, y_pred, average='macro')
    avg_recall.append(recall_fold)
    f1_fold = f1_score(y_true, y_pred, average='macro')
    avg_f1.append(f1_fold)
    print('Accuracy[{:.4f}] Recall[{:.4f}] F1[{:.4f}] at fold[{}]'.format(acc_fold, recall_fold, f1_fold ,i+1))
    print('________________________________________________________________')
    
  return avg_acc, avg_recall,avg_f1

In [0]:
def Train(X,y,folds):
  avg_acc = []
  avg_recall = []
  avg_f1 = []
  n_class = y.shape[1]
  _,_,img_rows, img_cols = X.shape
  print(X.shape)
  for i in range(0, len(folds)):
    train_idx = folds[i][0]
    test_idx = folds[i][1]
    X_train = X[train_idx]
    X_test = X[test_idx]
    model=build_model_1(img_rows,img_cols,n_class)
    print(model.summary)
    model.compile(loss='categorical_crossentropy', metrics=['accuracy'], optimizer='SGD')
    model.fit(X_train, y[train_idx], batch_size=64, epochs=300)
    y_pred = model.predict(X_test)
    y_pred = np.argmax(y_pred, axis=1)
    y_true = np.argmax(y[test_idx], axis=1)
    acc_fold = accuracy_score(y_true, y_pred)
    avg_acc.append(acc_fold)
    recall_fold = recall_score(y_true, y_pred, average='macro')
    avg_recall.append(recall_fold)
    f1_fold = f1_score(y_true, y_pred, average='macro')
    avg_f1.append(f1_fold)
    print('Accuracy[{:.4f}] Recall[{:.4f}] F1[{:.4f}] at fold[{}]'.format(acc_fold, recall_fold, f1_fold ,i+1))
    print('________________________________________________________________')
    
  return avg_acc, avg_recall,avg_f1

In [0]:
tf.keras.backend.set_image_data_format('channels_first')

In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOSO/MHEALTH.npz')

Streaming output truncated to the last 5000 lines.
Epoch 220/300
2292/2292 [==============================] - 0s 184us/sample - loss: 0.1213 - accuracy: 0.9825
Epoch 221/300
2292/2292 [==============================] - 0s 181us/sample - loss: 0.1230 - accuracy: 0.9821
Epoch 222/300
2292/2292 [==============================] - 0s 182us/sample - loss: 0.1214 - accuracy: 0.9830
Epoch 223/300
2292/2292 [==============================] - 0s 191us/sample - loss: 0.1198 - accuracy: 0.9821
Epoch 224/300
2292/2292 [==============================] - 0s 180us/sample - loss: 0.1217 - accuracy: 0.9825
Epoch 225/300
2292/2292 [==============================] - 0s 186us/sample - loss: 0.1199 - accuracy: 0.9847
Epoch 226/300
2292/2292 [==============================] - 0s 179us/sample - loss: 0.1197 - accuracy: 0.9847
Epoch 227/300
2292/2292 [==============================] - 0s 186us/sample - loss: 0.1190 - accuracy: 0.9856
Epoch 228/300
2292/2292 [==============================] - 0s 184us/sample - 

In [0]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOSO/MHEALTH.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
2292/2292 [==============================] - 0s 180us/sample - loss: 0.1473 - accuracy: 0.9699
Epoch 226/300
2292/2292 [==============================] - 0s 186us/sample - loss: 0.1466 - accuracy: 0.9703
Epoch 227/300
2292/2292 [==============================] - 0s 184us/sample - loss: 0.1454 - accuracy: 0.9703
Epoch 228/300
2292/2292 [==============================] - 0s 184us/sample - loss: 0.1443 - accuracy: 0.9699
Epoch 229/300
2292/2292 [==============================] - 0s 183us/sample - loss: 0.1435 - accuracy: 0.9708
Epoch 230/300
2292/2292 [==============================] - 0s 186us/sample - loss: 0.1423 - accuracy: 0.9708
Epoch 231/300
2292/2292 [==============================] - 0s 183us/sample - loss: 0.1413 - accuracy: 0.9708
Epoch 232/300
2292/2292 [==============================] - 0s 180us/sample - loss: 0.1406 - accuracy: 0.9712
Epoch 233/300
2292/2292 [==============================] - 0s 183us/sample - 

In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOSO/USCHAD.npz')

Streaming output truncated to the last 5000 lines.
Epoch 220/300
9147/9147 [==============================] - 1s 127us/sample - loss: 0.4183 - accuracy: 0.8465
Epoch 221/300
9147/9147 [==============================] - 1s 128us/sample - loss: 0.3771 - accuracy: 0.8625
Epoch 222/300
9147/9147 [==============================] - 1s 129us/sample - loss: 0.3796 - accuracy: 0.8604
Epoch 223/300
9147/9147 [==============================] - 1s 128us/sample - loss: 0.3725 - accuracy: 0.8619
Epoch 224/300
9147/9147 [==============================] - 1s 129us/sample - loss: 0.3992 - accuracy: 0.8507
Epoch 225/300
9147/9147 [==============================] - 1s 129us/sample - loss: 0.3717 - accuracy: 0.8614
Epoch 226/300
9147/9147 [==============================] - 1s 128us/sample - loss: 0.3943 - accuracy: 0.8548
Epoch 227/300
9147/9147 [==============================] - 1s 129us/sample - loss: 0.3969 - accuracy: 0.8485
Epoch 228/300
9147/9147 [==============================] - 1s 128us/sample - 

In [0]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOSO/USCHAD.npz')

In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD1_1s.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD1_1s.npz
(3771, 1, 50, 6)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f49b10dc2b0>>
Train on 3281 samples
Epoch 1/300
3281/3281 [==============================] - 3s 768us/sample - loss: 3.0452 - accuracy: 0.0454
Epoch 2/300
3281/3281 [==============================] - 0s 81us/sample - loss: 3.0425 - accuracy: 0.0518
Epoch 3/300
3281/3281 [==============================] - 0s 82us/sample - loss: 3.0399 - accuracy: 0.0552
Epoch 4/300
3281/3281 [==============================] - 0s 83us/sample - loss: 3.0372 - accuracy: 0.0591
Epoch 5/300
3281/3281 [==============================] - 0s 88us/sample - loss: 3.0346 - accuracy: 0.0616
Epoch 6/300
3281/3281 [==============================] - 0s 89us/sample - loss: 3.0322 - accuracy: 0.0677
Epoch 7/300
3281/3281 [==============================] - 0s 80us/sample - loss: 3.0298 - accuracy: 0.0713
Epoch 8/

In [0]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD1_1s.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD1_1s.npz
(3771, 1, 50, 6)
Train on 3281 samples
Epoch 1/300
3281/3281 [==============================] - 8s 2ms/sample - loss: 3.0456 - accuracy: 0.0524
Epoch 2/300
3281/3281 [==============================] - 0s 81us/sample - loss: 3.0385 - accuracy: 0.0625
Epoch 3/300
3281/3281 [==============================] - 0s 86us/sample - loss: 3.0346 - accuracy: 0.0704
Epoch 4/300
3281/3281 [==============================] - 0s 94us/sample - loss: 3.0288 - accuracy: 0.0698
Epoch 5/300
3281/3281 [==============================] - 0s 87us/sample - loss: 3.0245 - accuracy: 0.0853
Epoch 6/300
3281/3281 [==============================] - 0s 87us/sample - loss: 3.0216 - accuracy: 0.0923
Epoch 7/300
3281/3281 [==============================] - 0s 88us/sample - loss: 3.0162 - accuracy: 0.0957
Epoch 8/300
3281/3281 [==============================] - 0s 87us/sample - loss: 3.0104 - accuracy: 0.1116
Epoch 9/300
3281/3

In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD2_1s.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD2_1s.npz
(1137, 1, 50, 6)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f49b0f5e0f0>>
Train on 987 samples
Epoch 1/300
987/987 [==============================] - 2s 2ms/sample - loss: 1.7968 - accuracy: 0.1266
Epoch 2/300
987/987 [==============================] - 0s 97us/sample - loss: 1.7929 - accuracy: 0.1763
Epoch 3/300
987/987 [==============================] - 0s 84us/sample - loss: 1.7892 - accuracy: 0.2158
Epoch 4/300
987/987 [==============================] - 0s 86us/sample - loss: 1.7858 - accuracy: 0.2411
Epoch 5/300
987/987 [==============================] - 0s 90us/sample - loss: 1.7823 - accuracy: 0.2543
Epoch 6/300
987/987 [==============================] - 0s 87us/sample - loss: 1.7786 - accuracy: 0.2837
Epoch 7/300
987/987 [==============================] - 0s 89us/sample - loss: 1.7749 - accuracy: 0.3019
Epoch 8/300
987/987 [====

In [0]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD2_1s.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/LOSO/UTD-MHAD2_1s.npz
(1137, 1, 50, 6)
Train on 987 samples
Epoch 1/300
987/987 [==============================] - 2s 2ms/sample - loss: 1.7938 - accuracy: 0.1702
Epoch 2/300
987/987 [==============================] - 0s 87us/sample - loss: 1.7907 - accuracy: 0.1793
Epoch 3/300
987/987 [==============================] - 0s 89us/sample - loss: 1.7876 - accuracy: 0.1955
Epoch 4/300
987/987 [==============================] - 0s 90us/sample - loss: 1.7846 - accuracy: 0.2107
Epoch 5/300
987/987 [==============================] - 0s 98us/sample - loss: 1.7818 - accuracy: 0.2270
Epoch 6/300
987/987 [==============================] - 0s 89us/sample - loss: 1.7789 - accuracy: 0.2391
Epoch 7/300
987/987 [==============================] - 0s 100us/sample - loss: 1.7762 - accuracy: 0.2472
Epoch 8/300
987/987 [==============================] - 0s 90us/sample - loss: 1.7735 - accuracy: 0.2472
Epoch 9/300
987/987 [=============

In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOSO/WHARF.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/LOSO/WHARF.npz
(3871, 1, 160, 3)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f49b2cb6320>>
Train on 2189 samples
Epoch 1/300
2189/2189 [==============================] - 2s 932us/sample - loss: 2.4472 - accuracy: 0.2736
Epoch 2/300
2189/2189 [==============================] - 0s 92us/sample - loss: 2.3332 - accuracy: 0.3134
Epoch 3/300
2189/2189 [==============================] - 0s 105us/sample - loss: 2.1995 - accuracy: 0.3134
Epoch 4/300
2189/2189 [==============================] - 0s 117us/sample - loss: 2.1031 - accuracy: 0.3138
Epoch 5/300
2189/2189 [==============================] - 0s 94us/sample - loss: 2.0327 - accuracy: 0.3221
Epoch 6/300
2189/2189 [==============================] - 0s 92us/sample - loss: 1.9716 - accuracy: 0.3577
Epoch 7/300
2189/2189 [==============================] - 0s 96us/sample - loss: 1.9234 - accuracy: 0.3773
Epoch 8/300


/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy[0.4439] Recall[0.2251] F1[0.2345] at fold[2]
________________________________________________________________
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f4a02a37f98>>
Train on 3756 samples
Epoch 1/300
3756/3756 [==============================] - 2s 563us/sample - loss: 2.4478 - accuracy: 0.1861
Epoch 2/300
3756/3756 [==============================] - 0s 87us/sample - loss: 2.3649 - accuracy: 0.2740
Epoch 3/300
3756/3756 [==============================] - 0s 89us/sample - loss: 2.2718 - accuracy: 0.2622
Epoch 4/300
3756/3756 [==============================] - 0s 90us/sample - loss: 2.1794 - accuracy: 0.2758
Epoch 5/300
3756/3756 [==============================] - 0s 89us/sample - loss: 2.0985 - accuracy: 0.3232
Epoch 6/300
3756/3756 [==============================] - 0s 93us/sample - loss: 2.0225 - accuracy: 0.3743
Epoch 7/300
3756/3756 [==============================] - 0s 92us/sample - loss: 1.9599 - accuracy: 0.3908
Ep

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy[0.5161] Recall[0.3073] F1[0.2406] at fold[4]
________________________________________________________________
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f49ac9e7b38>>
Train on 3864 samples
Epoch 1/300
3864/3864 [==============================] - 2s 543us/sample - loss: 2.4734 - accuracy: 0.1431
Epoch 2/300
3864/3864 [==============================] - 0s 86us/sample - loss: 2.4451 - accuracy: 0.2420
Epoch 3/300
3864/3864 [==============================] - 0s 87us/sample - loss: 2.4197 - accuracy: 0.2591
Epoch 4/300
3864/3864 [==============================] - 0s 95us/sample - loss: 2.3968 - accuracy: 0.2604
Epoch 5/300
3864/3864 [==============================] - 0s 101us/sample - loss: 2.3744 - accuracy: 0.2604
Epoch 6/300
3864/3864 [==============================] - 0s 95us/sample - loss: 2.3493 - accuracy: 0.2604
Epoch 7/300
3864/3864 [==============================] - 0s 89us/sample - loss: 2.3180 - accuracy: 0.2604
E

...

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy[0.0000] Recall[0.0000] F1[0.0000] at fold[14]
________________________________________________________________
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f49b184b908>>
Train on 3833 samples
Epoch 1/300
3833/3833 [==============================] - 2s 524us/sample - loss: 2.3748 - accuracy: 0.2648
Epoch 2/300
3833/3833 [==============================] - 0s 88us/sample - loss: 2.2812 - accuracy: 0.2768
Epoch 3/300
3833/3833 [==============================] - 0s 96us/sample - loss: 2.2018 - accuracy: 0.3081
Epoch 4/300
3833/3833 [==============================] - 0s 95us/sample - loss: 2.1389 - accuracy: 0.3532
Epoch 5/300
3833/3833 [==============================] - 0s 92us/sample - loss: 2.0779 - accuracy: 0.3587
Epoch 6/300
3833/3833 [==============================] - 0s 93us/sample - loss: 2.0238 - accuracy: 0.3658
Epoch 7/300
3833/3833 [==============================] - 0s 90us/sample - loss: 1.9821 - accuracy: 0.3676
E

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy[0.4474] Recall[0.0559] F1[0.0773] at fold[15]
________________________________________________________________
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f49b13cea58>>
Train on 3837 samples
Epoch 1/300
3837/3837 [==============================] - 2s 561us/sample - loss: 2.4020 - accuracy: 0.2223
Epoch 2/300
3837/3837 [==============================] - 0s 91us/sample - loss: 2.3004 - accuracy: 0.2622
Epoch 3/300
3837/3837 [==============================] - 0s 92us/sample - loss: 2.2254 - accuracy: 0.2622
Epoch 4/300
3837/3837 [==============================] - 0s 104us/sample - loss: 2.1616 - accuracy: 0.2624
Epoch 5/300
3837/3837 [==============================] - 0s 101us/sample - loss: 2.1046 - accuracy: 0.3039
Epoch 6/300
3837/3837 [==============================] - 0s 88us/sample - loss: 2.0512 - accuracy: 0.3393
Epoch 7/300
3837/3837 [==============================] - 0s 88us/sample - loss: 2.0055 - accuracy: 0.3654

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [0]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOSO/WHARF.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/LOSO/WHARF.npz
(3871, 1, 160, 3)
Train on 2189 samples
Epoch 1/300
2189/2189 [==============================] - 2s 903us/sample - loss: 2.3972 - accuracy: 0.2709
Epoch 2/300
2189/2189 [==============================] - 0s 86us/sample - loss: 2.2485 - accuracy: 0.3138
Epoch 3/300
2189/2189 [==============================] - 0s 89us/sample - loss: 2.1569 - accuracy: 0.3207
Epoch 4/300
2189/2189 [==============================] - 0s 98us/sample - loss: 2.0794 - accuracy: 0.3248
Epoch 5/300
2189/2189 [==============================] - 0s 93us/sample - loss: 2.0180 - accuracy: 0.3280
Epoch 6/300
2189/2189 [==============================] - 0s 95us/sample - loss: 1.9685 - accuracy: 0.3417
Epoch 7/300
2189/2189 [==============================] - 0s 88us/sample - loss: 1.9369 - accuracy: 0.3518
Epoch 8/300
2189/2189 [==============================] - 0s 86us/sample - loss: 1.8891 - accuracy: 0.3773
Epoch 9/300
2189/2189 

/usr/local/lib/python3.6/dist-packages/hpelm/nnets/slfn_python.py:65: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  B = np.linalg.lstsq(HH, HT)[0]


Accuracy[0.1908] Recall[0.0884] F1[0.0384] at fold[1]
________________________________________________________________
Train on 3684 samples
Epoch 1/300
3684/3684 [==============================] - 2s 544us/sample - loss: 2.4743 - accuracy: 0.1246
Epoch 2/300
3684/3684 [==============================] - 0s 88us/sample - loss: 2.4456 - accuracy: 0.2405
Epoch 3/300
3684/3684 [==============================] - 0s 86us/sample - loss: 2.4202 - accuracy: 0.2685
Epoch 4/300
3684/3684 [==============================] - 0s 86us/sample - loss: 2.3977 - accuracy: 0.2685
Epoch 5/300
3684/3684 [==============================] - 0s 90us/sample - loss: 2.3780 - accuracy: 0.2685
Epoch 6/300
3684/3684 [==============================] - 0s 86us/sample - loss: 2.3608 - accuracy: 0.2685
Epoch 7/300
3684/3684 [==============================] - 0s 86us/sample - loss: 2.3458 - accuracy: 0.2685
Epoch 8/300
3684/3684 [==============================] - 0s 91us/sample - loss: 2.3328 - accuracy: 0.2685
Epoch 9/30

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Train on 3756 samples
Epoch 1/300
3756/3756 [==============================] - 3s 777us/sample - loss: 2.4703 - accuracy: 0.1672
Epoch 2/300
3756/3756 [==============================] - 0s 97us/sample - loss: 2.3572 - accuracy: 0.2628
Epoch 3/300
3756/3756 [==============================] - 0s 87us/sample - loss: 2.2415 - accuracy: 0.2721
Epoch 4/300
3756/3756 [==============================] - 0s 84us/sample - loss: 2.1555 - accuracy: 0.3317
Epoch 5/300
3756/3756 [==============================] - 0s 89us/sample - loss: 2.0811 - accuracy: 0.3538
Epoch 6/300
3756/3756 [==============================] - 0s 90us/sample - loss: 2.0217 - accuracy: 0.3605
Epoch 7/300
3756/3756 [==============================] - 0s 93us/sample - loss: 1.9688 - accuracy: 0.3621
Epoch 8/300
3756/3756 [==============================] - 0s 96us/sample - loss: 1.9213 - accuracy: 0.3613
Epoch 9/300
3756/3756 [==============================] - 0s 85us/sample - loss: 1.8859 - accuracy: 0.3738
Epoch 10/300
3756/3756 

...

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Train on 3833 samples
Epoch 1/300
3833/3833 [==============================] - 2s 555us/sample - loss: 2.4128 - accuracy: 0.2786
Epoch 2/300
3833/3833 [==============================] - 0s 95us/sample - loss: 2.3060 - accuracy: 0.3128
Epoch 3/300
3833/3833 [==============================] - 0s 87us/sample - loss: 2.2192 - accuracy: 0.3024
Epoch 4/300
3833/3833 [==============================] - 0s 83us/sample - loss: 2.1481 - accuracy: 0.3167
Epoch 5/300
3833/3833 [==============================] - 0s 96us/sample - loss: 2.0898 - accuracy: 0.3452
Epoch 6/300
3833/3833 [==============================] - 0s 91us/sample - loss: 2.0443 - accuracy: 0.3551
Epoch 7/300
3833/3833 [==============================] - 0s 81us/sample - loss: 2.0123 - accuracy: 0.3671
Epoch 8/300
3833/3833 [==============================] - 0s 99us/sample - loss: 1.9678 - accuracy: 0.3900
Epoch 9/300
3833/3833 [==============================] - 0s 87us/sample - loss: 1.9401 - accuracy: 0.4208
Epoch 10/300
3833/3833 

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Train on 3837 samples
Epoch 1/300
3837/3837 [==============================] - 2s 539us/sample - loss: 2.3647 - accuracy: 0.2971
Epoch 2/300
3837/3837 [==============================] - 0s 87us/sample - loss: 2.2520 - accuracy: 0.3159
Epoch 3/300
3837/3837 [==============================] - 0s 88us/sample - loss: 2.1685 - accuracy: 0.3260
Epoch 4/300
3837/3837 [==============================] - 0s 87us/sample - loss: 2.0967 - accuracy: 0.3474
Epoch 5/300
3837/3837 [==============================] - 0s 91us/sample - loss: 2.0343 - accuracy: 0.3563
Epoch 6/300
3837/3837 [==============================] - 0s 91us/sample - loss: 1.9797 - accuracy: 0.3698
Epoch 7/300
3837/3837 [==============================] - 0s 84us/sample - loss: 1.9333 - accuracy: 0.3951
Epoch 8/300
3837/3837 [==============================] - 0s 89us/sample - loss: 1.9041 - accuracy: 0.4287
Epoch 9/300
3837/3837 [==============================] - 0s 89us/sample - loss: 1.8672 - accuracy: 0.4389
Epoch 10/300
3837/3837 

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOSO/WISDM.npz')

NameError: ignored

In [0]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOSO/WISDM.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/LOSO/WISDM.npz
(20846, 1, 100, 3)
Train on 20167 samples
Epoch 1/300
20167/20167 [==============================] - 4s 177us/sample - loss: 1.6518 - accuracy: 0.3886
Epoch 2/300
20167/20167 [==============================] - 2s 87us/sample - loss: 1.5061 - accuracy: 0.4295
Epoch 3/300
20167/20167 [==============================] - 2s 87us/sample - loss: 1.4263 - accuracy: 0.5026
Epoch 4/300
20167/20167 [==============================] - 2s 82us/sample - loss: 1.3031 - accuracy: 0.5978
Epoch 5/300
20167/20167 [==============================] - 2s 83us/sample - loss: 1.1098 - accuracy: 0.6861
Epoch 6/300
20167/20167 [==============================] - 2s 84us/sample - loss: 0.9190 - accuracy: 0.7619
Epoch 7/300
20167/20167 [==============================] - 2s 88us/sample - loss: 0.7764 - accuracy: 0.7833
Epoch 8/300
20167/20167 [==============================] - 2s 82us/sample - loss: 0.6771 - accuracy: 0.7977
Epoc

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy[0.7874] Recall[0.4529] F1[0.4849] at fold[2]
________________________________________________________________
Train on 20215 samples
Epoch 1/300
20215/20215 [==============================] - 4s 222us/sample - loss: 1.6485 - accuracy: 0.3857
Epoch 2/300
20215/20215 [==============================] - 2s 88us/sample - loss: 1.4558 - accuracy: 0.4184
Epoch 3/300
20215/20215 [==============================] - 2s 85us/sample - loss: 1.3319 - accuracy: 0.4874
Epoch 4/300
20215/20215 [==============================] - 2s 85us/sample - loss: 1.2441 - accuracy: 0.5629
Epoch 5/300
20215/20215 [==============================] - 2s 88us/sample - loss: 1.1714 - accuracy: 0.6071
Epoch 6/300
20215/20215 [==============================] - 2s 90us/sample - loss: 1.1054 - accuracy: 0.6444
Epoch 7/300
20215/20215 [==============================] - 2s 82us/sample - loss: 1.0436 - accuracy: 0.6746
Epoch 8/300
20215/20215 [==============================] - 2s 90us/sample - loss: 0.9887 - accuracy: 

/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Accuracy[0.3870] Recall[0.2171] F1[0.1820] at fold[5]
________________________________________________________________
Train on 20362 samples
Epoch 1/300
20362/20362 [==============================] - 3s 169us/sample - loss: 1.6350 - accuracy: 0.3995
Epoch 2/300
20362/20362 [==============================] - 2s 85us/sample - loss: 1.4145 - accuracy: 0.4614
Epoch 3/300
20362/20362 [==============================] - 2s 88us/sample - loss: 1.2888 - accuracy: 0.5633
Epoch 4/300
20362/20362 [==============================] - 2s 85us/sample - loss: 1.1628 - accuracy: 0.6611
Epoch 5/300
20362/20362 [==============================] - 2s 88us/sample - loss: 1.0367 - accuracy: 0.7071
Epoch 6/300
20362/20362 [==============================] - 2s 87us/sample - loss: 0.9337 - accuracy: 0.7203
Epoch 7/300
20362/20362 [==============================] - 2s 88us/sample - loss: 0.8614 - accuracy: 0.7270
Epoch 8/300
20362/20362 [==============================] - 2s 84us/sample - loss: 0.8114 - accuracy: 

In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/FNOW/MHEALTH.npz')

Panwar  et al. 2015 /content/drive/My Drive/Computer_vision_project/data/FNOW/MHEALTH.npz
(1335, 1, 250, 23)
Accuracy[0.0889] Recall[0.0833] F1[0.0136] at fold[1]
________________________________________________________________
Accuracy[0.0889] Recall[0.0833] F1[0.0136] at fold[2]
________________________________________________________________
Accuracy[0.0896] Recall[0.0833] F1[0.0137] at fold[3]
________________________________________________________________
Accuracy[0.0896] Recall[0.0833] F1[0.0137] at fold[4]
________________________________________________________________
Accuracy[0.0896] Recall[0.0833] F1[0.0137] at fold[5]
________________________________________________________________
Accuracy[0.0902] Recall[0.0833] F1[0.0138] at fold[6]
________________________________________________________________
Accuracy[0.0902] Recall[0.0833] F1[0.0138] at fold[7]
________________________________________________________________
Accuracy[0.0902] Recall[0.0833] F1[0.0138] at fold[8]
____

In [18]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/FNOW/MHEALTH.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
1200/1200 [==============================] - 0s 146us/sample - loss: 0.4976 - accuracy: 0.9600
Epoch 226/300
1200/1200 [==============================] - 0s 146us/sample - loss: 0.4940 - accuracy: 0.9600
Epoch 227/300
1200/1200 [==============================] - 0s 146us/sample - loss: 0.4907 - accuracy: 0.9592
Epoch 228/300
1200/1200 [==============================] - 0s 169us/sample - loss: 0.4870 - accuracy: 0.9600
Epoch 229/300
1200/1200 [==============================] - 0s 152us/sample - loss: 0.4831 - accuracy: 0.9608
Epoch 230/300
1200/1200 [==============================] - 0s 156us/sample - loss: 0.4788 - accuracy: 0.9608
Epoch 231/300
1200/1200 [==============================] - 0s 147us/sample - loss: 0.4756 - accuracy: 0.9608
Epoch 232/300
1200/1200 [==============================] - 0s 155us/sample - loss: 0.4719 - accuracy: 0.9608
Epoch 233/300
1200/1200 [==============================] - 0s 143us/sample - 

In [19]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/FNOW/UTD-MHAD1_1s.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
1835/1835 [==============================] - 0s 118us/sample - loss: 2.2450 - accuracy: 0.5548
Epoch 226/300
1835/1835 [==============================] - 0s 113us/sample - loss: 2.2379 - accuracy: 0.5520
Epoch 227/300
1835/1835 [==============================] - 0s 114us/sample - loss: 2.2339 - accuracy: 0.5608
Epoch 228/300
1835/1835 [==============================] - 0s 111us/sample - loss: 2.2358 - accuracy: 0.5575
Epoch 229/300
1835/1835 [==============================] - 0s 108us/sample - loss: 2.2333 - accuracy: 0.5515
Epoch 230/300
1835/1835 [==============================] - 0s 121us/sample - loss: 2.2286 - accuracy: 0.5580
Epoch 231/300
1835/1835 [==============================] - 0s 112us/sample - loss: 2.2232 - accuracy: 0.5537
Epoch 232/300
1835/1835 [==============================] - 0s 123us/sample - loss: 2.2186 - accuracy: 0.5531
Epoch 233/300
1835/1835 [==============================] - 0s 126us/sample - 

In [20]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/FNOW/UTD-MHAD2_1s.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
553/553 [==============================] - 0s 157us/sample - loss: 1.1576 - accuracy: 0.8879
Epoch 226/300
553/553 [==============================] - 0s 122us/sample - loss: 1.1521 - accuracy: 0.8915
Epoch 227/300
553/553 [==============================] - 0s 119us/sample - loss: 1.1466 - accuracy: 0.8969
Epoch 228/300
553/553 [==============================] - 0s 135us/sample - loss: 1.1413 - accuracy: 0.8969
Epoch 229/300
553/553 [==============================] - 0s 120us/sample - loss: 1.1359 - accuracy: 0.9024
Epoch 230/300
553/553 [==============================] - 0s 115us/sample - loss: 1.1305 - accuracy: 0.9042
Epoch 231/300
553/553 [==============================] - 0s 150us/sample - loss: 1.1253 - accuracy: 0.9060
Epoch 232/300
553/553 [==============================] - 0s 138us/sample - loss: 1.1201 - accuracy: 0.9060
Epoch 233/300
553/553 [==============================] - 0s 123us/sample - loss: 1.1157 - acc

In [21]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/FNOW/WHARF.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/FNOW/WHARF.npz
(2146, 1, 160, 3)
Train on 1926 samples
Epoch 1/300
1926/1926 [==============================] - 3s 2ms/sample - loss: 2.4284 - accuracy: 0.2399
Epoch 2/300
1926/1926 [==============================] - 0s 114us/sample - loss: 2.3749 - accuracy: 0.2477
Epoch 3/300
1926/1926 [==============================] - 0s 127us/sample - loss: 2.3306 - accuracy: 0.2471
Epoch 4/300
1926/1926 [==============================] - 0s 132us/sample - loss: 2.2983 - accuracy: 0.2466
Epoch 5/300
1926/1926 [==============================] - 0s 130us/sample - loss: 2.2829 - accuracy: 0.2466
Epoch 6/300
1926/1926 [==============================] - 0s 127us/sample - loss: 2.2543 - accuracy: 0.2466
Epoch 7/300
1926/1926 [==============================] - 0s 135us/sample - loss: 2.2279 - accuracy: 0.2466
Epoch 8/300
1926/1926 [==============================] - 0s 124us/sample - loss: 2.2011 - accuracy: 0.2471
Epoch 9/300
1926/

/usr/local/lib/python3.6/dist-packages/hpelm/nnets/slfn_python.py:65: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  B = np.linalg.lstsq(HH, HT)[0]


Train on 1927 samples
Epoch 1/300
1927/1927 [==============================] - 3s 1ms/sample - loss: 2.4781 - accuracy: 0.1344
Epoch 2/300
1927/1927 [==============================] - 0s 129us/sample - loss: 2.4445 - accuracy: 0.2387
Epoch 3/300
1927/1927 [==============================] - 0s 137us/sample - loss: 2.4003 - accuracy: 0.2584
Epoch 4/300
1927/1927 [==============================] - 0s 133us/sample - loss: 2.3517 - accuracy: 0.2766
Epoch 5/300
1927/1927 [==============================] - 0s 128us/sample - loss: 2.3051 - accuracy: 0.2989
Epoch 6/300
1927/1927 [==============================] - 0s 125us/sample - loss: 2.2616 - accuracy: 0.3140
Epoch 7/300
1927/1927 [==============================] - 0s 130us/sample - loss: 2.2227 - accuracy: 0.3243
Epoch 8/300
1927/1927 [==============================] - 0s 124us/sample - loss: 2.1876 - accuracy: 0.3285
Epoch 9/300
1927/1927 [==============================] - 0s 134us/sample - loss: 2.1543 - accuracy: 0.3342
Epoch 10/300
1927

/usr/local/lib/python3.6/dist-packages/hpelm/nnets/slfn_python.py:65: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  B = np.linalg.lstsq(HH, HT)[0]


Train on 1927 samples
Epoch 1/300
1927/1927 [==============================] - 3s 1ms/sample - loss: 2.4773 - accuracy: 0.1692
Epoch 2/300
1927/1927 [==============================] - 0s 124us/sample - loss: 2.4613 - accuracy: 0.2455
Epoch 3/300
1927/1927 [==============================] - 0s 136us/sample - loss: 2.4447 - accuracy: 0.2501
Epoch 4/300
1927/1927 [==============================] - 0s 129us/sample - loss: 2.4259 - accuracy: 0.2491
Epoch 5/300
1927/1927 [==============================] - 0s 132us/sample - loss: 2.3999 - accuracy: 0.2465
Epoch 6/300
1927/1927 [==============================] - 0s 125us/sample - loss: 2.3651 - accuracy: 0.2465
Epoch 7/300
1927/1927 [==============================] - 0s 127us/sample - loss: 2.3235 - accuracy: 0.2465
Epoch 8/300
1927/1927 [==============================] - 0s 120us/sample - loss: 2.2712 - accuracy: 0.2522
Epoch 9/300
1927/1927 [==============================] - 0s 132us/sample - loss: 2.2104 - accuracy: 0.2771
Epoch 10/300
1927

/usr/local/lib/python3.6/dist-packages/hpelm/nnets/slfn_python.py:65: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  B = np.linalg.lstsq(HH, HT)[0]


Train on 1929 samples
Epoch 1/300
1929/1929 [==============================] - 3s 1ms/sample - loss: 2.4267 - accuracy: 0.2608
Epoch 2/300
1929/1929 [==============================] - 0s 116us/sample - loss: 2.3529 - accuracy: 0.2644
Epoch 3/300
1929/1929 [==============================] - 0s 114us/sample - loss: 2.2943 - accuracy: 0.2597
Epoch 4/300
1929/1929 [==============================] - 0s 114us/sample - loss: 2.2471 - accuracy: 0.2732
Epoch 5/300
1929/1929 [==============================] - 0s 118us/sample - loss: 2.2045 - accuracy: 0.2924
Epoch 6/300
1929/1929 [==============================] - 0s 127us/sample - loss: 2.1663 - accuracy: 0.3033
Epoch 7/300
1929/1929 [==============================] - 0s 123us/sample - loss: 2.1331 - accuracy: 0.3162
Epoch 8/300
1929/1929 [==============================] - 0s 125us/sample - loss: 2.1052 - accuracy: 0.3281
Epoch 9/300
1929/1929 [==============================] - 0s 123us/sample - loss: 2.0773 - accuracy: 0.3359
Epoch 10/300
1929

/usr/local/lib/python3.6/dist-packages/hpelm/nnets/slfn_python.py:65: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  B = np.linalg.lstsq(HH, HT)[0]


Train on 1938 samples
Epoch 1/300
1938/1938 [==============================] - 3s 2ms/sample - loss: 2.4780 - accuracy: 0.1429
Epoch 2/300
1938/1938 [==============================] - 0s 127us/sample - loss: 2.4622 - accuracy: 0.2379
Epoch 3/300
1938/1938 [==============================] - 0s 134us/sample - loss: 2.4420 - accuracy: 0.2456
Epoch 4/300
1938/1938 [==============================] - 0s 120us/sample - loss: 2.4151 - accuracy: 0.2461
Epoch 5/300
1938/1938 [==============================] - 0s 129us/sample - loss: 2.3812 - accuracy: 0.2456
Epoch 6/300
1938/1938 [==============================] - 0s 132us/sample - loss: 2.3351 - accuracy: 0.2456
Epoch 7/300
1938/1938 [==============================] - 0s 125us/sample - loss: 2.2709 - accuracy: 0.2456
Epoch 8/300
1938/1938 [==============================] - 0s 129us/sample - loss: 2.2157 - accuracy: 0.2456
Epoch 9/300
1938/1938 [==============================] - 0s 118us/sample - loss: 2.1673 - accuracy: 0.2575
Epoch 10/300
1938

In [31]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/FNOW/MHEALTH.npz')

Streaming output truncated to the last 5000 lines.
Epoch 220/300
1200/1200 [==============================] - 0s 158us/sample - loss: 0.5053 - accuracy: 0.9533
Epoch 221/300
1200/1200 [==============================] - 0s 162us/sample - loss: 0.5016 - accuracy: 0.9533
Epoch 222/300
1200/1200 [==============================] - 0s 171us/sample - loss: 0.4980 - accuracy: 0.9533
Epoch 223/300
1200/1200 [==============================] - 0s 149us/sample - loss: 0.4946 - accuracy: 0.9533
Epoch 224/300
1200/1200 [==============================] - 0s 152us/sample - loss: 0.4916 - accuracy: 0.9533
Epoch 225/300
1200/1200 [==============================] - 0s 161us/sample - loss: 0.4883 - accuracy: 0.9542
Epoch 226/300
1200/1200 [==============================] - 0s 161us/sample - loss: 0.4853 - accuracy: 0.9542
Epoch 227/300
1200/1200 [==============================] - 0s 162us/sample - loss: 0.4820 - accuracy: 0.9542
Epoch 228/300
1200/1200 [==============================] - 0s 172us/sample - 

In [33]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/FNOW/UTD-MHAD1_1s.npz')

Streaming output truncated to the last 5000 lines.
Epoch 220/300
1835/1835 [==============================] - 0s 114us/sample - loss: 2.4000 - accuracy: 0.3793
Epoch 221/300
1835/1835 [==============================] - 0s 129us/sample - loss: 2.3944 - accuracy: 0.3755
Epoch 222/300
1835/1835 [==============================] - 0s 129us/sample - loss: 2.3910 - accuracy: 0.3798
Epoch 223/300
1835/1835 [==============================] - 0s 126us/sample - loss: 2.3834 - accuracy: 0.3815
Epoch 224/300
1835/1835 [==============================] - 0s 125us/sample - loss: 2.3793 - accuracy: 0.3738
Epoch 225/300
1835/1835 [==============================] - 0s 114us/sample - loss: 2.3721 - accuracy: 0.3798
Epoch 226/300
1835/1835 [==============================] - 0s 117us/sample - loss: 2.3750 - accuracy: 0.3853
Epoch 227/300
1835/1835 [==============================] - 0s 121us/sample - loss: 2.3722 - accuracy: 0.3880
Epoch 228/300
1835/1835 [==============================] - 0s 123us/sample - 

In [34]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/FNOW/UTD-MHAD2_1s.npz')

Streaming output truncated to the last 5000 lines.
Epoch 220/300
553/553 [==============================] - 0s 131us/sample - loss: 1.0777 - accuracy: 0.9042
Epoch 221/300
553/553 [==============================] - 0s 132us/sample - loss: 1.0716 - accuracy: 0.9078
Epoch 222/300
553/553 [==============================] - 0s 132us/sample - loss: 1.0657 - accuracy: 0.9114
Epoch 223/300
553/553 [==============================] - 0s 139us/sample - loss: 1.0597 - accuracy: 0.9132
Epoch 224/300
553/553 [==============================] - 0s 136us/sample - loss: 1.0537 - accuracy: 0.9132
Epoch 225/300
553/553 [==============================] - 0s 134us/sample - loss: 1.0478 - accuracy: 0.9132
Epoch 226/300
553/553 [==============================] - 0s 131us/sample - loss: 1.0419 - accuracy: 0.9168
Epoch 227/300
553/553 [==============================] - 0s 118us/sample - loss: 1.0363 - accuracy: 0.9186
Epoch 228/300
553/553 [==============================] - 0s 137us/sample - loss: 1.0306 - acc

In [35]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/FNOW/WHARF.npz')

Streaming output truncated to the last 5000 lines.
Epoch 220/300
1927/1927 [==============================] - 0s 126us/sample - loss: 1.4434 - accuracy: 0.5008
Epoch 221/300
1927/1927 [==============================] - 0s 114us/sample - loss: 1.4322 - accuracy: 0.5018
Epoch 222/300
1927/1927 [==============================] - 0s 140us/sample - loss: 1.4403 - accuracy: 0.5018
Epoch 223/300
1927/1927 [==============================] - 0s 133us/sample - loss: 1.4203 - accuracy: 0.5044
Epoch 224/300
1927/1927 [==============================] - 0s 124us/sample - loss: 1.4285 - accuracy: 0.5003
Epoch 225/300
1927/1927 [==============================] - 0s 129us/sample - loss: 1.4234 - accuracy: 0.5143
Epoch 226/300
1927/1927 [==============================] - 0s 123us/sample - loss: 1.4080 - accuracy: 0.5080
Epoch 227/300
1927/1927 [==============================] - 0s 123us/sample - loss: 1.4096 - accuracy: 0.5179
Epoch 228/300
1927/1927 [==============================] - 0s 119us/sample - 

In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/FNOW/WISDM.npz')

In [22]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOTO/MHEALTH.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
2298/2298 [==============================] - 0s 158us/sample - loss: 0.1462 - accuracy: 0.9639
Epoch 226/300
2298/2298 [==============================] - 0s 178us/sample - loss: 0.1444 - accuracy: 0.9634
Epoch 227/300
2298/2298 [==============================] - 0s 171us/sample - loss: 0.1428 - accuracy: 0.9652
Epoch 228/300
2298/2298 [==============================] - 0s 159us/sample - loss: 0.1510 - accuracy: 0.9630
Epoch 229/300
2298/2298 [==============================] - 0s 160us/sample - loss: 0.1462 - accuracy: 0.9669
Epoch 230/300
2298/2298 [==============================] - 0s 167us/sample - loss: 0.1446 - accuracy: 0.9700
Epoch 231/300
2298/2298 [==============================] - 0s 161us/sample - loss: 0.1450 - accuracy: 0.9674
Epoch 232/300
2298/2298 [==============================] - 0s 172us/sample - loss: 0.1440 - accuracy: 0.9661
Epoch 233/300
2298/2298 [==============================] - 0s 162us/sample - 

In [23]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD1_1s.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
3299/3299 [==============================] - 0s 130us/sample - loss: 1.9877 - accuracy: 0.4562
Epoch 226/300
3299/3299 [==============================] - 0s 121us/sample - loss: 1.9748 - accuracy: 0.4604
Epoch 227/300
3299/3299 [==============================] - 0s 122us/sample - loss: 1.9756 - accuracy: 0.4471
Epoch 228/300
3299/3299 [==============================] - 0s 128us/sample - loss: 1.9650 - accuracy: 0.4644
Epoch 229/300
3299/3299 [==============================] - 0s 121us/sample - loss: 1.9741 - accuracy: 0.4610
Epoch 230/300
3299/3299 [==============================] - 0s 125us/sample - loss: 1.9661 - accuracy: 0.4607
Epoch 231/300
3299/3299 [==============================] - 0s 124us/sample - loss: 1.9508 - accuracy: 0.4777
Epoch 232/300
3299/3299 [==============================] - 0s 119us/sample - loss: 1.9579 - accuracy: 0.4741
Epoch 233/300
3299/3299 [==============================] - 0s 128us/sample - 

In [24]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD2_1s.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
1009/1009 [==============================] - 0s 131us/sample - loss: 0.6708 - accuracy: 0.8315
Epoch 226/300
1009/1009 [==============================] - 0s 121us/sample - loss: 0.6649 - accuracy: 0.8295
Epoch 227/300
1009/1009 [==============================] - 0s 125us/sample - loss: 0.6637 - accuracy: 0.8295
Epoch 228/300
1009/1009 [==============================] - 0s 121us/sample - loss: 0.6592 - accuracy: 0.8365
Epoch 229/300
1009/1009 [==============================] - 0s 118us/sample - loss: 0.6538 - accuracy: 0.8345
Epoch 230/300
1009/1009 [==============================] - 0s 116us/sample - loss: 0.6492 - accuracy: 0.8295
Epoch 231/300
1009/1009 [==============================] - 0s 114us/sample - loss: 0.6440 - accuracy: 0.8256
Epoch 232/300
1009/1009 [==============================] - 0s 114us/sample - loss: 0.6399 - accuracy: 0.8276
Epoch 233/300
1009/1009 [==============================] - 0s 116us/sample - 

In [25]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/LOTO/WHARF.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
3456/3456 [==============================] - 0s 118us/sample - loss: 1.1827 - accuracy: 0.6097
Epoch 226/300
3456/3456 [==============================] - 0s 118us/sample - loss: 1.1845 - accuracy: 0.6082
Epoch 227/300
3456/3456 [==============================] - 0s 107us/sample - loss: 1.1771 - accuracy: 0.6091
Epoch 228/300
3456/3456 [==============================] - 0s 119us/sample - loss: 1.1829 - accuracy: 0.6102
Epoch 229/300
3456/3456 [==============================] - 0s 111us/sample - loss: 1.1784 - accuracy: 0.6123
Epoch 230/300
3456/3456 [==============================] - 0s 119us/sample - loss: 1.1902 - accuracy: 0.6024
Epoch 231/300
3456/3456 [==============================] - 0s 122us/sample - loss: 1.1907 - accuracy: 0.6039
Epoch 232/300
3456/3456 [==============================] - 0s 118us/sample - loss: 1.1803 - accuracy: 0.6085
Epoch 233/300
3456/3456 [==============================] - 0s 120us/sample - 

In [0]:
RunPanware('/content/drive/My Drive/Computer_vision_project/data/LOTO/MHEALTH.npz')

Panwar  et al. 2015 /content/drive/My Drive/Computer_vision_project/data/LOTO/MHEALTH.npz
(2555, 1, 250, 23)
Accuracy[0.0898] Recall[0.0833] F1[0.0137] at fold[1]
________________________________________________________________
Accuracy[0.0895] Recall[0.0833] F1[0.0137] at fold[2]
________________________________________________________________
Accuracy[0.0858] Recall[0.0833] F1[0.0132] at fold[3]
________________________________________________________________
Accuracy[0.0902] Recall[0.0833] F1[0.0138] at fold[4]
________________________________________________________________
Accuracy[0.0875] Recall[0.0833] F1[0.0134] at fold[5]
________________________________________________________________
Accuracy[0.0836] Recall[0.0833] F1[0.0129] at fold[6]
________________________________________________________________
Accuracy[0.0885] Recall[0.0833] F1[0.0135] at fold[7]
________________________________________________________________
Accuracy[0.1004] Recall[0.0833] F1[0.0152] at fold[8]
____

In [0]:
RunPanware('/content/drive/My Drive/Computer_vision_project/data/LOTO/USCHAD.npz')


Panwar  et al. 2015 /content/drive/My Drive/Computer_vision_project/data/LOTO/USCHAD.npz
(9824, 1, 500, 6)
Accuracy[0.1645] Recall[0.0833] F1[0.0235] at fold[1]
________________________________________________________________
Accuracy[0.1282] Recall[0.0833] F1[0.0189] at fold[2]
________________________________________________________________
Accuracy[0.1295] Recall[0.0833] F1[0.0191] at fold[3]
________________________________________________________________
Accuracy[0.1308] Recall[0.0833] F1[0.0193] at fold[4]
________________________________________________________________
Accuracy[0.1176] Recall[0.0833] F1[0.0175] at fold[5]
________________________________________________________________
Accuracy[0.1250] Recall[0.0833] F1[0.0185] at fold[6]
________________________________________________________________
Accuracy[0.1350] Recall[0.0833] F1[0.0198] at fold[7]
________________________________________________________________
Accuracy[0.1888] Recall[0.0833] F1[0.0265] at fold[8]
______

In [0]:
RunPanware('/content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD1_1s.npz')


Panwar  et al. 2015 /content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD1_1s.npz
(3771, 1, 50, 6)
Accuracy[0.0475] Recall[0.0476] F1[0.0043] at fold[1]
________________________________________________________________
Accuracy[0.0530] Recall[0.0476] F1[0.0048] at fold[2]
________________________________________________________________
Accuracy[0.0546] Recall[0.0476] F1[0.0049] at fold[3]
________________________________________________________________
Accuracy[0.0532] Recall[0.0476] F1[0.0048] at fold[4]
________________________________________________________________
Accuracy[0.0582] Recall[0.0476] F1[0.0052] at fold[5]
________________________________________________________________
Accuracy[0.0551] Recall[0.0476] F1[0.0050] at fold[6]
________________________________________________________________
Accuracy[0.0532] Recall[0.0476] F1[0.0048] at fold[7]
________________________________________________________________
Accuracy[0.0529] Recall[0.0476] F1[0.0048] at fold[8]
_

/usr/local/lib/python3.6/dist-packages/scipy/stats/_distn_infrastructure.py:2003: RuntimeWarning: invalid value encountered in multiply
  lower_bound = _a * scale + loc
/usr/local/lib/python3.6/dist-packages/scipy/stats/_distn_infrastructure.py:2004: RuntimeWarning: invalid value encountered in multiply
  upper_bound = _b * scale + loc


In [0]:
RunPanware('/content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD2_1s.npz')


Panwar  et al. 2015 /content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD2_1s.npz
(1137, 1, 50, 6)
Accuracy[0.5449] Recall[0.5840] F1[0.5478] at fold[1]
________________________________________________________________
Accuracy[0.5781] Recall[0.5502] F1[0.5385] at fold[2]
________________________________________________________________
Accuracy[0.6415] Recall[0.6743] F1[0.6457] at fold[3]
________________________________________________________________
Accuracy[0.6100] Recall[0.6110] F1[0.5960] at fold[4]
________________________________________________________________
Accuracy[0.1504] Recall[0.1667] F1[0.0436] at fold[5]
________________________________________________________________
Accuracy[0.1545] Recall[0.1667] F1[0.0446] at fold[6]
________________________________________________________________
Accuracy[0.5536] Recall[0.5886] F1[0.5561] at fold[7]
________________________________________________________________
Accuracy[0.6300] Recall[0.6214] F1[0.6060] at fold[8]
_

In [0]:
RunPanware('/content/drive/My Drive/Computer_vision_project/data/SNOW/MHEALTH.npz')

Panwar  et al. 2015 /content/drive/My Drive/Computer_vision_project/data/SNOW/MHEALTH.npz
(2555, 1, 250, 23)
Accuracy[0.0891] Recall[0.0833] F1[0.0136] at fold[1]
________________________________________________________________
Accuracy[0.0898] Recall[0.0833] F1[0.0137] at fold[2]
________________________________________________________________
Accuracy[0.0898] Recall[0.0833] F1[0.0137] at fold[3]
________________________________________________________________
Accuracy[0.0898] Recall[0.0833] F1[0.0137] at fold[4]
________________________________________________________________
Accuracy[0.0902] Recall[0.0833] F1[0.0138] at fold[5]
________________________________________________________________
Accuracy[0.0902] Recall[0.0833] F1[0.0138] at fold[6]
________________________________________________________________
Accuracy[0.0902] Recall[0.0833] F1[0.0138] at fold[7]
________________________________________________________________
Accuracy[0.0902] Recall[0.0833] F1[0.0138] at fold[8]
____

In [0]:
RunPanware('/content/drive/My Drive/Computer_vision_project/data/SNOW/USCHAD.npz')

Panwar  et al. 2015 /content/drive/My Drive/Computer_vision_project/data/SNOW/USCHAD.npz
(9824, 1, 500, 6)
Accuracy[0.1377] Recall[0.0833] F1[0.0202] at fold[1]
________________________________________________________________
Accuracy[0.1377] Recall[0.0833] F1[0.0202] at fold[2]
________________________________________________________________
Accuracy[0.1379] Recall[0.0833] F1[0.0202] at fold[3]
________________________________________________________________
Accuracy[0.1381] Recall[0.0833] F1[0.0202] at fold[4]
________________________________________________________________
Accuracy[0.1386] Recall[0.0833] F1[0.0203] at fold[5]
________________________________________________________________
Accuracy[0.1388] Recall[0.0833] F1[0.0203] at fold[6]
________________________________________________________________
Accuracy[0.1389] Recall[0.0833] F1[0.0203] at fold[7]
________________________________________________________________
Accuracy[0.1389] Recall[0.0833] F1[0.0203] at fold[8]
______

In [0]:
RunPanware('/content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD1_1s.npz')

Panwar  et al. 2015 /content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD1_1s.npz
(3771, 1, 50, 6)
Accuracy[0.0519] Recall[0.0476] F1[0.0047] at fold[1]
________________________________________________________________
Accuracy[0.0524] Recall[0.0476] F1[0.0047] at fold[2]
________________________________________________________________
Accuracy[0.0525] Recall[0.0476] F1[0.0048] at fold[3]
________________________________________________________________
Accuracy[0.0525] Recall[0.0476] F1[0.0048] at fold[4]
________________________________________________________________
Accuracy[0.0526] Recall[0.0476] F1[0.0048] at fold[5]
________________________________________________________________
Accuracy[0.0531] Recall[0.0476] F1[0.0048] at fold[6]
________________________________________________________________
Accuracy[0.0532] Recall[0.0476] F1[0.0048] at fold[7]
________________________________________________________________
Accuracy[0.0509] Recall[0.0476] F1[0.0046] at fold[8]
_

/usr/local/lib/python3.6/dist-packages/scipy/stats/_distn_infrastructure.py:2003: RuntimeWarning: invalid value encountered in multiply
  lower_bound = _a * scale + loc
/usr/local/lib/python3.6/dist-packages/scipy/stats/_distn_infrastructure.py:2004: RuntimeWarning: invalid value encountered in multiply
  upper_bound = _b * scale + loc


In [0]:
RunPanware('/content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD2_1s.npz')

Panwar  et al. 2015 /content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD2_1s.npz
(1137, 1, 50, 6)
Accuracy[0.4831] Recall[0.4840] F1[0.4543] at fold[1]
________________________________________________________________
Accuracy[0.5763] Recall[0.5662] F1[0.5718] at fold[2]
________________________________________________________________
Accuracy[0.5603] Recall[0.5230] F1[0.5351] at fold[3]
________________________________________________________________
Accuracy[0.6460] Recall[0.6304] F1[0.6388] at fold[4]
________________________________________________________________
Accuracy[0.5268] Recall[0.5076] F1[0.5148] at fold[5]
________________________________________________________________
Accuracy[0.1518] Recall[0.1667] F1[0.0439] at fold[6]
________________________________________________________________
Accuracy[0.5625] Recall[0.5759] F1[0.5638] at fold[7]
________________________________________________________________
Accuracy[0.5893] Recall[0.6036] F1[0.5699] at fold[8]
_

In [26]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/SNOW/MHEALTH.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
2299/2299 [==============================] - 0s 161us/sample - loss: 0.1539 - accuracy: 0.9635
Epoch 226/300
2299/2299 [==============================] - 0s 181us/sample - loss: 0.1519 - accuracy: 0.9674
Epoch 227/300
2299/2299 [==============================] - 0s 176us/sample - loss: 0.1535 - accuracy: 0.9656
Epoch 228/300
2299/2299 [==============================] - 0s 160us/sample - loss: 0.1530 - accuracy: 0.9652
Epoch 229/300
2299/2299 [==============================] - 0s 174us/sample - loss: 0.1552 - accuracy: 0.9613
Epoch 230/300
2299/2299 [==============================] - 0s 168us/sample - loss: 0.1535 - accuracy: 0.9643
Epoch 231/300
2299/2299 [==============================] - 0s 172us/sample - loss: 0.1511 - accuracy: 0.9622
Epoch 232/300
2299/2299 [==============================] - 0s 175us/sample - loss: 0.1533 - accuracy: 0.9630
Epoch 233/300
2299/2299 [==============================] - 0s 181us/sample - 

In [27]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/SNOW/USCHAD.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/SNOW/USCHAD.npz
(9824, 1, 500, 6)
Train on 8836 samples
Epoch 1/300
7936/8836 [=========================>....] - ETA: 0s - loss: 2.4766 - accuracy: 0.0983

KeyboardInterrupt: ignored

In [28]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD1_1s.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
3389/3389 [==============================] - 0s 116us/sample - loss: 2.0363 - accuracy: 0.4400
Epoch 226/300
3389/3389 [==============================] - 0s 120us/sample - loss: 2.0306 - accuracy: 0.4423
Epoch 227/300
3389/3389 [==============================] - 0s 129us/sample - loss: 2.0422 - accuracy: 0.4408
Epoch 228/300
3389/3389 [==============================] - 0s 120us/sample - loss: 2.0320 - accuracy: 0.4488
Epoch 229/300
3389/3389 [==============================] - 0s 122us/sample - loss: 2.0228 - accuracy: 0.4473
Epoch 230/300
3389/3389 [==============================] - 0s 117us/sample - loss: 2.0307 - accuracy: 0.4509
Epoch 231/300
3389/3389 [==============================] - 0s 113us/sample - loss: 2.0270 - accuracy: 0.4394
Epoch 232/300
3389/3389 [==============================] - 0s 121us/sample - loss: 2.0256 - accuracy: 0.4432
Epoch 233/300
3389/3389 [==============================] - 0s 115us/sample - 

In [29]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/SNOW/UTD-MHAD2_1s.npz')

Streaming output truncated to the last 5000 lines.
Epoch 225/300
1019/1019 [==============================] - 0s 124us/sample - loss: 0.5848 - accuracy: 0.9401
Epoch 226/300
1019/1019 [==============================] - 0s 111us/sample - loss: 0.5797 - accuracy: 0.9401
Epoch 227/300
1019/1019 [==============================] - 0s 116us/sample - loss: 0.5753 - accuracy: 0.9411
Epoch 228/300
1019/1019 [==============================] - 0s 136us/sample - loss: 0.5694 - accuracy: 0.9441
Epoch 229/300
1019/1019 [==============================] - 0s 139us/sample - loss: 0.5648 - accuracy: 0.9450
Epoch 230/300
1019/1019 [==============================] - 0s 113us/sample - loss: 0.5609 - accuracy: 0.9450
Epoch 231/300
1019/1019 [==============================] - 0s 110us/sample - loss: 0.5585 - accuracy: 0.9450
Epoch 232/300
1019/1019 [==============================] - 0s 118us/sample - loss: 0.5559 - accuracy: 0.9441
Epoch 233/300
1019/1019 [==============================] - 0s 133us/sample - 

In [30]:
RunJian_Sun_ELM('/content/drive/My Drive/Computer_vision_project/data/SNOW/WHARF.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/SNOW/WHARF.npz
(3880, 1, 160, 3)
Train on 3485 samples
Epoch 1/300
3485/3485 [==============================] - 4s 1ms/sample - loss: 2.3965 - accuracy: 0.2829
Epoch 2/300
3485/3485 [==============================] - 0s 117us/sample - loss: 2.3071 - accuracy: 0.2657
Epoch 3/300
3485/3485 [==============================] - 0s 122us/sample - loss: 2.2382 - accuracy: 0.2611
Epoch 4/300
3485/3485 [==============================] - 0s 116us/sample - loss: 2.1800 - accuracy: 0.2617
Epoch 5/300
3485/3485 [==============================] - 0s 116us/sample - loss: 2.1270 - accuracy: 0.2864
Epoch 6/300
3485/3485 [==============================] - 0s 123us/sample - loss: 2.0831 - accuracy: 0.2999
Epoch 7/300
3485/3485 [==============================] - 0s 115us/sample - loss: 2.0409 - accuracy: 0.3412
Epoch 8/300
3485/3485 [==============================] - 0s 118us/sample - loss: 2.0076 - accuracy: 0.3590
Epoch 9/300
3485/

/usr/local/lib/python3.6/dist-packages/hpelm/nnets/slfn_python.py:65: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  B = np.linalg.lstsq(HH, HT)[0]


Train on 3493 samples
Epoch 1/300
3493/3493 [==============================] - 3s 774us/sample - loss: 2.4753 - accuracy: 0.1351
Epoch 2/300
3493/3493 [==============================] - 0s 119us/sample - loss: 2.4494 - accuracy: 0.2388
Epoch 3/300
3493/3493 [==============================] - 0s 121us/sample - loss: 2.4262 - accuracy: 0.2617
Epoch 4/300
3493/3493 [==============================] - 0s 123us/sample - loss: 2.4058 - accuracy: 0.2605
Epoch 5/300
3493/3493 [==============================] - 0s 121us/sample - loss: 2.3876 - accuracy: 0.2597
Epoch 6/300
3493/3493 [==============================] - 0s 120us/sample - loss: 2.3716 - accuracy: 0.2594
Epoch 7/300
3493/3493 [==============================] - 0s 128us/sample - loss: 2.3573 - accuracy: 0.2594
Epoch 8/300
3493/3493 [==============================] - 0s 124us/sample - loss: 2.3445 - accuracy: 0.2594
Epoch 9/300
3493/3493 [==============================] - 0s 132us/sample - loss: 2.3331 - accuracy: 0.2594
Epoch 10/300
34

/usr/local/lib/python3.6/dist-packages/hpelm/nnets/slfn_python.py:65: FutureWarning: `rcond` parameter will change to the default of machine precision times ``max(M, N)`` where M and N are the input matrix dimensions.
To use the future default and silence this warning we advise to pass `rcond=None`, to keep using the old, explicitly pass `rcond=-1`.
  B = np.linalg.lstsq(HH, HT)[0]


Accuracy[0.2687] Recall[0.1008] F1[0.0659] at fold[7]
________________________________________________________________
Train on 3495 samples
Epoch 1/300
3495/3495 [==============================] - 4s 1ms/sample - loss: 2.3875 - accuracy: 0.2635
Epoch 2/300
3495/3495 [==============================] - 0s 114us/sample - loss: 2.3021 - accuracy: 0.2595
Epoch 3/300
3495/3495 [==============================] - 0s 121us/sample - loss: 2.2393 - accuracy: 0.2595
Epoch 4/300
3495/3495 [==============================] - 0s 125us/sample - loss: 2.1855 - accuracy: 0.2595
Epoch 5/300
3495/3495 [==============================] - 0s 130us/sample - loss: 2.1347 - accuracy: 0.2595
Epoch 6/300
3495/3495 [==============================] - 0s 123us/sample - loss: 2.0953 - accuracy: 0.2884
Epoch 7/300
3495/3495 [==============================] - 0s 116us/sample - loss: 2.0563 - accuracy: 0.3579
Epoch 8/300
3495/3495 [==============================] - 0s 131us/sample - loss: 2.0240 - accuracy: 0.3788
Epoch

In [36]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOTO/MHEALTH.npz')

Streaming output truncated to the last 5000 lines.
Epoch 220/300
2298/2298 [==============================] - 0s 160us/sample - loss: 0.1025 - accuracy: 0.9891
Epoch 221/300
2298/2298 [==============================] - 0s 167us/sample - loss: 0.1016 - accuracy: 0.9896
Epoch 222/300
2298/2298 [==============================] - 0s 168us/sample - loss: 0.1006 - accuracy: 0.9896
Epoch 223/300
2298/2298 [==============================] - 0s 160us/sample - loss: 0.0996 - accuracy: 0.9900
Epoch 224/300
2298/2298 [==============================] - 0s 159us/sample - loss: 0.0987 - accuracy: 0.9900
Epoch 225/300
2298/2298 [==============================] - 0s 164us/sample - loss: 0.0977 - accuracy: 0.9900
Epoch 226/300
2298/2298 [==============================] - 0s 167us/sample - loss: 0.0969 - accuracy: 0.9900
Epoch 227/300
2298/2298 [==============================] - 0s 169us/sample - loss: 0.0960 - accuracy: 0.9900
Epoch 228/300
2298/2298 [==============================] - 0s 160us/sample - 

In [37]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD1_1s.npz')

Streaming output truncated to the last 5000 lines.
Epoch 220/300
3299/3299 [==============================] - 0s 122us/sample - loss: 2.2855 - accuracy: 0.3437
Epoch 221/300
3299/3299 [==============================] - 0s 112us/sample - loss: 2.2848 - accuracy: 0.3304
Epoch 222/300
3299/3299 [==============================] - 0s 122us/sample - loss: 2.2860 - accuracy: 0.3289
Epoch 223/300
3299/3299 [==============================] - 0s 121us/sample - loss: 2.3090 - accuracy: 0.3143
Epoch 224/300
3299/3299 [==============================] - 0s 116us/sample - loss: 2.2872 - accuracy: 0.3268
Epoch 225/300
3299/3299 [==============================] - 0s 124us/sample - loss: 2.2887 - accuracy: 0.3240
Epoch 226/300
3299/3299 [==============================] - 0s 115us/sample - loss: 2.2750 - accuracy: 0.3337
Epoch 227/300
3299/3299 [==============================] - 0s 121us/sample - loss: 2.2941 - accuracy: 0.3201
Epoch 228/300
3299/3299 [==============================] - 0s 122us/sample - 

In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD2_1s.npz')

Jian Sun et al. 2018 /content/drive/My Drive/Computer_vision_project/data/LOTO/UTD-MHAD2_1s.npz
(1137, 1, 50, 6)
<bound method Network.summary of <tensorflow.python.keras.engine.sequential.Sequential object at 0x7f4f303862b0>>
Train on 981 samples
Epoch 1/300
981/981 [==============================] - 2s 2ms/sample - loss: 1.7894 - accuracy: 0.2059
Epoch 2/300
981/981 [==============================] - 0s 108us/sample - loss: 1.7810 - accuracy: 0.2457
Epoch 3/300
981/981 [==============================] - 0s 110us/sample - loss: 1.7731 - accuracy: 0.2824
Epoch 4/300
981/981 [==============================] - 0s 111us/sample - loss: 1.7659 - accuracy: 0.2966
Epoch 5/300
981/981 [==============================] - 0s 113us/sample - loss: 1.7593 - accuracy: 0.3160
Epoch 6/300
981/981 [==============================] - 0s 114us/sample - loss: 1.7528 - accuracy: 0.3374
Epoch 7/300
981/981 [==============================] - 0s 116us/sample - loss: 1.7466 - accuracy: 0.3619
Epoch 8/300
981/981

In [0]:
RunJian_Sun('/content/drive/My Drive/Computer_vision_project/data/LOTO/WHARF.npz')